In [40]:
# İmport necessary libraries
import pandas as pd
import warnings
import numpy as np
from datetime import datetime
from dateutil.relativedelta import relativedelta, MO
warnings.filterwarnings("ignore")

In [41]:
#Read and ddrop Unnamed:0 column.
df = pd.read_csv("eom_all (2).csv")
df.drop(["Unnamed: 0"], axis=1, inplace=True)

In [42]:
#Convert trd_exctn_dt column to datetime format.
df["trd_exctn_dt"] = pd.to_datetime(df["trd_exctn_dt"])
#Clean rows if INTEREST_FREQUENCY is not bigger than 0.
df = df[df["INTEREST_FREQUENCY"] >= 0]

In [43]:
zeros = df[df["INTEREST_FREQUENCY"] == 0]

In [44]:
#Drop rows that contains NaN
df.dropna(inplace=True)
#Drop cusip id's that has only 1 row.
df = df[df.groupby("cusip_id").cusip_id.transform("count") > 1]

In [45]:
#Sort values and reset-set index.
df = df.sort_values("cusip_id")
df = df.reset_index().sort_values("index")
df.set_index("index", inplace=True) 

In [46]:
df.INTEREST_FREQUENCY.dtype

dtype('float64')

In [47]:
#Convert INTEREST_FREQUENCY column to appropriate format.
df["INTEREST_FREQUENCY"] = df["INTEREST_FREQUENCY"].astype("int")
df["INTEREST_FREQUENCY"] = df["INTEREST_FREQUENCY"].astype("str")
df["INTEREST_FREQUENCY"].replace({"2": "6", "4": "3", "1": "12", "12": "1"}, inplace=True)
df["INTEREST_FREQUENCY"] = df["INTEREST_FREQUENCY"].astype("int")

In [48]:
# Function that clears non-consecutive rows for each cusip id.
def Cleaner(df):
 qf = pd.DataFrame()
 for mf in df['cusip_id'].unique():
    
    zf = df[df['cusip_id'] == mf]
    
    dt = zf['trd_exctn_dt']
    
    mzf = zf.loc[(((dt.dt.month - dt.shift(-1).dt.month).abs() == 1)  |  (dt.dt.month - dt.shift(1).dt.month.abs() == 1))
                | ((dt.dt.month - dt.shift(-1).dt.month).abs() == 11)  | ((dt.dt.year - dt.shift(1).dt.year) == 1 )]   
   
    qf=pd.concat([qf,mzf],axis=0)
 return qf

In [49]:
# Convert FIRST_INTEREST_DATE and LAST_INTEREST_DATE to datetime format.
df["FIRST_INTEREST_DATE"] = df["FIRST_INTEREST_DATE"].astype(int)
df["LAST_INTEREST_DATE"] = df["LAST_INTEREST_DATE"].astype(int)

df["FIRST_INTEREST_DATE"] = pd.to_datetime(df.FIRST_INTEREST_DATE, format="%Y%m%d")
df["LAST_INTEREST_DATE"] = pd.to_datetime(df.LAST_INTEREST_DATE, format="%Y%m%d")

In [50]:
# Reset index again because after data cleaning indexes changed.
df = df.reset_index()
df.drop(["index"], axis=1, inplace=True)

In [51]:
df = Cleaner(df)

In [52]:
df['C'] = 0

In [53]:
#define dataframe for work on it.
zf = pd.DataFrame()
count=0
for m in df["cusip_id"].unique():    
    
    #df for unique cusip_id 
    mf = df.loc[df["cusip_id"] == m]    
    
    
    #pd.Series for dates
    dates = mf['trd_exctn_dt'].reset_index(drop=True)   
    
    mf = mf.sort_values('trd_exctn_dt')  
    
    
    #Defining dates.
    start = mf.FIRST_INTEREST_DATE.iloc[0]
    end = mf.LAST_INTEREST_DATE.iloc[0]
    freq = mf.INTEREST_FREQUENCY.iloc[0]
   
    paid = []
    paid.append(start)
    x = start
    while x < end:
        x = x + relativedelta(months=+(freq))
        paid.append(x)
  
    #for each pair of dates in the dates series

    for i in range(dates.shape[0]-1):
        pastmonth, pastyear = dates[i].month, dates[i].year
        nowmonth, nowyear = dates[i+1].month, dates[i+1].year
        
        # if date pair is suitable to work on 
        if ((pastmonth + 1 == nowmonth) & (pastyear == nowyear)) |  ((pastyear +1 == nowyear) & (pastmonth-11 == nowmonth)):
            #Check if the paid dates fall within the appropriate ranges.
            for j in paid:
                #For those who fall within certain ranges from the paid dates, make column c of the larger date in the pair 1
                if (dates[i] < j < dates[i+1]) == 1 :  
                    mf["C"].loc[mf["trd_exctn_dt"] == dates[i+1]] = 1
                    
    
    zf = pd.concat([zf, mf], axis=0)  

In [54]:
zf.C.value_counts()

0    5457
1     937
Name: C, dtype: int64

In [55]:
#Convert object type to integer.
zf['INTEREST_FREQUENCY']  = zf['INTEREST_FREQUENCY'].astype('int')

In [56]:
#Calculate coupon_amt column.
zf['coupon_amt'] = (zf['COUPON'] * zf['PRINCIPAL_AMT']) / (zf['INTEREST_FREQUENCY'] * 1000)

In [57]:
#Calculate total_value.
zf['total_value'] = zf['dirty_price'] + zf['coupon_amt']

In [58]:
zf

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
0     00138GAA7   2021-02-08  20130711.0          2014-01-01   
1     00138GAA7   2021-03-29  20130711.0          2014-01-01   
2     00138GAA7   2021-04-21  20130711.0          2014-01-01   
4     00138GAA7   2021-11-02  20130711.0          2014-01-01   
5     00138GAA7   2021-12-06  20130711.0          2014-01-01   
...         ...          ...         ...                 ...   
6713  989822AA9   2021-08-25  19931020.0          1994-04-15   
6714  989822AA9   2021-09-27  19931020.0          1994-04-15   
6715  989822AA9   2021-10-27  19931020.0          1994-04-15   
6716  989822AA9   2021-11-22  19931020.0          1994-04-15   
6717  989822AA9   2021-12-29  19931020.0          1994-04-15   

      INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  \
0                      6         2030-01-01  20300701.0   8.500   
1                      6         2030-01-01  20300701.0   8.500   
2                      6         2030-01-01  20300701.0   8.500   
4                      6         2030-01-01  20300701.0   8.500   
5                      6         2030-01-01  20300701.0   8.500   
...                  ...                ...         ...     ...   
6713                   6         2023-04-15  20231015.0   7.125   
6714                   6         2023-04-15  20231015.0   7.125   
6715                   6         2023-04-15  20231015.0   7.125   
6716                   6         2023-04-15  20231015.0   7.125   
6717                   6         2023-04-15  20231015.0   7.125   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  
0         146.937000         1000.0   147.397417  0    1.416667   148.814083  
1         139.235000         1000.0   140.285694  0    1.416667   141.702361  
2         138.031500         1000.0   139.353722  0    1.416667   140.770389  
4         140.721333         1000.0   142.173417  0    1.416667   143.590083  
5         138.706111         1000.0   140.559583  0    1.416667   141.976250  
...              ...            ...          ... ..         ...          ...  
6713      112.963000         1000.0   114.269250  0    1.187500   115.456750  
6714      112.439667         1000.0   114.062583  0    1.187500   115.250083  
6715      111.964333         1000.0   112.389854  1    1.187500   113.577354  
6716      111.102636         1000.0   111.488574  0    1.187500   112.676074  
6717      110.458000         1000.0   111.200187  0    1.187500   112.387687  

[6394 rows x 14 columns]

In [59]:
#Set a value for returns.
zf['returns'] = -99

In [69]:
#define dataframe for work on it.
mzf = pd.DataFrame()

for m in zf["cusip_id"].unique():

    #df for unique cusip_id 
    mf = zf.loc[zf["cusip_id"] == m]
    
    display(mf)
    
    #pd.Series for dates
    dates = mf['trd_exctn_dt'].reset_index(drop=True) 
    display(dates)
    
    for i in range(dates.shape[0]-1):
        pastmonth, pastyear = dates[i].month, dates[i].year
        nowmonth, nowyear = dates[i+1].month, dates[i+1].year
        
        # if date pair is suitable to work on 
        if ((pastmonth + 1 == nowmonth) & (pastyear == nowyear)) |  ((pastyear +1 == nowyear) & (pastmonth-11 == nowmonth)):
            past = mf.loc[mf["trd_exctn_dt"] == dates[i]]['total_value'].iloc[0]
            now = mf.loc[mf["trd_exctn_dt"] == dates[i+1]]['total_value'].iloc[0]           
            mf["returns"].loc[mf["trd_exctn_dt"] == dates[i+1]] = now/past
            
    mzf = pd.concat([mzf, mf], axis=0)

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  INTEREST_FREQUENCY  \
0  00138GAA7   2021-02-08  20130711.0          2014-01-01                   6   
1  00138GAA7   2021-03-29  20130711.0          2014-01-01                   6   
2  00138GAA7   2021-04-21  20130711.0          2014-01-01                   6   
4  00138GAA7   2021-11-02  20130711.0          2014-01-01                   6   
5  00138GAA7   2021-12-06  20130711.0          2014-01-01                   6   

  LAST_INTEREST_DATE    MATURITY  COUPON  daily_clean_pr  PRINCIPAL_AMT  \
0         2030-01-01  20300701.0     8.5      146.937000         1000.0   
1         2030-01-01  20300701.0     8.5      139.235000         1000.0   
2         2030-01-01  20300701.0     8.5      138.031500         1000.0   
4         2030-01-01  20300701.0     8.5      140.721333         1000.0   
5         2030-01-01  20300701.0     8.5      138.706111         1000.0   

   dirty_price  C  coupon_amt  total_value  returns  
0   147.397417  0    1.416667   148.814083      -99  
1   140.285694  0    1.416667   141.702361      -99  
2   139.353722  0    1.416667   140.770389      -99  
4   142.173417  0    1.416667   143.590083      -99  
5   140.559583  0    1.416667   141.976250      -99

0   2021-02-08
1   2021-03-29
2   2021-04-21
3   2021-11-02
4   2021-12-06
Name: trd_exctn_dt, dtype: datetime64[ns]

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  INTEREST_FREQUENCY  \
6  001814AQ5   2021-01-04  19940215.0          1994-08-15                   6   
7  001814AQ5   2021-02-16  19940215.0          1994-08-15                   6   
8  001814AQ5   2021-03-29  19940215.0          1994-08-15                   6   

  LAST_INTEREST_DATE    MATURITY  COUPON  daily_clean_pr  PRINCIPAL_AMT  \
6         2023-08-15  20240215.0   7.375      120.333500         1000.0   
7         2023-08-15  20240215.0   7.375      119.367333         1000.0   
8         2023-08-15  20240215.0   7.375      117.227889         1000.0   

   dirty_price  C  coupon_amt  total_value  returns  
6   120.548604  0    1.229167   121.777771      -99  
7   119.705354  1    1.229167   120.934521      -99  
8   117.688827  0    1.229167   118.917993      -99

0   2021-01-04
1   2021-02-16
2   2021-03-29
Name: trd_exctn_dt, dtype: datetime64[ns]

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
12  001814AR3   2021-01-20  19911104.0          1992-05-01   
13  001814AR3   2021-02-24  19911104.0          1992-05-01   
14  001814AR3   2021-03-25  19911104.0          1992-05-01   
15  001814AR3   2021-04-28  19911104.0          1992-05-01   
16  001814AR3   2021-05-26  19911104.0          1992-05-01   
17  001814AR3   2021-06-08  19911104.0          1992-05-01   
18  001814AR3   2021-07-27  19911104.0          1992-05-01   

    INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  daily_clean_pr  \
12                   6         2021-05-01  20211101.0   9.625      106.411000   
13                   6         2021-05-01  20211101.0   9.625      106.150667   
14                   6         2021-05-01  20211101.0   9.625      105.388000   
15                   6         2021-05-01  20211101.0   9.625      104.634600   
16                   6         2021-05-01  20211101.0   9.625      103.913375   
17                   6         2021-05-01  20211101.0   9.625      103.576282   
18                   6         2021-05-01  20211101.0   9.625      102.221771   

    PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  returns  
12         1000.0   107.092771  0    1.604167   108.696937      -99  
13         1000.0   106.885910  0    1.604167   108.490076      -99  
14         1000.0   106.123243  0    1.604167   107.727410      -99  
15         1000.0   105.423316  0    1.604167   107.027482      -99  
16         1000.0   104.675354  1    1.604167   106.279521      -99  
17         1000.0   104.097636  0    1.604167   105.701803      -99  
18         1000.0   103.398160  0    1.604167   105.002327      -99

...

0   2021-01-28
1   2021-02-10
Name: trd_exctn_dt, dtype: datetime64[ns]

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
6702  98920AAA6   2021-01-25  20180827.0          2019-02-27   
6703  98920AAA6   2021-02-16  20180827.0          2019-02-27   
6704  98920AAA6   2021-03-24  20180827.0          2019-02-27   
6705  98920AAA6   2021-04-14  20180827.0          2019-02-27   

      INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  \
6702                   6         2021-02-27  20210827.0     3.5   
6703                   6         2021-02-27  20210827.0     3.5   
6704                   6         2021-02-27  20210827.0     3.5   
6705                   6         2021-02-27  20210827.0     3.5   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
6702      101.808810         1000.0   101.954643  0    0.583333   102.537976   
6703      101.348000         1000.0   101.450083  0    0.583333   102.033417   
6704      101.269000         1000.0   101.409972  1    0.583333   101.993306   
6705      101.153522         1000.0   101.391716  0    0.583333   101.975050   

      returns  
6702      -99  
6703      -99  
6704      -99  
6705      -99

0   2021-01-25
1   2021-02-16
2   2021-03-24
3   2021-04-14
Name: trd_exctn_dt, dtype: datetime64[ns]

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
6706  989822AA9   2021-01-26  19931020.0          1994-04-15   
6707  989822AA9   2021-02-24  19931020.0          1994-04-15   
6708  989822AA9   2021-03-29  19931020.0          1994-04-15   
6709  989822AA9   2021-04-28  19931020.0          1994-04-15   
6710  989822AA9   2021-05-26  19931020.0          1994-04-15   
6711  989822AA9   2021-06-28  19931020.0          1994-04-15   
6712  989822AA9   2021-07-28  19931020.0          1994-04-15   
6713  989822AA9   2021-08-25  19931020.0          1994-04-15   
6714  989822AA9   2021-09-27  19931020.0          1994-04-15   
6715  989822AA9   2021-10-27  19931020.0          1994-04-15   
6716  989822AA9   2021-11-22  19931020.0          1994-04-15   
6717  989822AA9   2021-12-29  19931020.0          1994-04-15   

      INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  \
6706                   6         2023-04-15  20231015.0   7.125   
6707                   6         2023-04-15  20231015.0   7.125   
6708                   6         2023-04-15  20231015.0   7.125   
6709                   6         2023-04-15  20231015.0   7.125   
6710                   6         2023-04-15  20231015.0   7.125   
6711                   6         2023-04-15  20231015.0   7.125   
6712                   6         2023-04-15  20231015.0   7.125   
6713                   6         2023-04-15  20231015.0   7.125   
6714                   6         2023-04-15  20231015.0   7.125   
6715                   6         2023-04-15  20231015.0   7.125   
6716                   6         2023-04-15  20231015.0   7.125   
6717                   6         2023-04-15  20231015.0   7.125   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
6706      116.344762         1000.0   116.770283  0      1.1875   117.957783   
6707      115.577300         1000.0   115.983029  0      1.1875   117.170529   
6708      115.494000         1000.0   115.939312  0      1.1875   117.126812   
6709      114.279000         1000.0   114.724312  1      1.1875   115.911812   
6710      114.485319         1000.0   114.910840  0      1.1875   116.098340   
6711      114.076000         1000.0   114.818187  0      1.1875   116.005687   
6712      113.334088         1000.0   114.373151  0      1.1875   115.560651   
6713      112.963000         1000.0   114.269250  0      1.1875   115.456750   
6714      112.439667         1000.0   114.062583  0      1.1875   115.250083   
6715      111.964333         1000.0   112.389854  1      1.1875   113.577354   
6716      111.102636         1000.0   111.488574  0      1.1875   112.676074   
6717      110.458000         1000.0   111.200187  0      1.1875   112.387687   

      returns  
6706      -99  
6707      -99  
6708      -99  
6709      -99  
6710      -99  
6711      -99  
6712      -99  
6713      -99  
6714      -99  
6715      -99  
6716      -99  
6717      -99

0    2021-01-26
1    2021-02-24
2    2021-03-29
3    2021-04-28
4    2021-05-26
5    2021-06-28
6    2021-07-28
7    2021-08-25
8    2021-09-27
9    2021-10-27
10   2021-11-22
11   2021-12-29
Name: trd_exctn_dt, dtype: datetime64[ns]

In [61]:
mzf

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
0     00138GAA7   2021-02-08  20130711.0          2014-01-01   
1     00138GAA7   2021-03-29  20130711.0          2014-01-01   
2     00138GAA7   2021-04-21  20130711.0          2014-01-01   
4     00138GAA7   2021-11-02  20130711.0          2014-01-01   
5     00138GAA7   2021-12-06  20130711.0          2014-01-01   
...         ...          ...         ...                 ...   
6713  989822AA9   2021-08-25  19931020.0          1994-04-15   
6714  989822AA9   2021-09-27  19931020.0          1994-04-15   
6715  989822AA9   2021-10-27  19931020.0          1994-04-15   
6716  989822AA9   2021-11-22  19931020.0          1994-04-15   
6717  989822AA9   2021-12-29  19931020.0          1994-04-15   

      INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  \
0                      6         2030-01-01  20300701.0   8.500   
1                      6         2030-01-01  20300701.0   8.500   
2                      6         2030-01-01  20300701.0   8.500   
4                      6         2030-01-01  20300701.0   8.500   
5                      6         2030-01-01  20300701.0   8.500   
...                  ...                ...         ...     ...   
6713                   6         2023-04-15  20231015.0   7.125   
6714                   6         2023-04-15  20231015.0   7.125   
6715                   6         2023-04-15  20231015.0   7.125   
6716                   6         2023-04-15  20231015.0   7.125   
6717                   6         2023-04-15  20231015.0   7.125   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
0         146.937000         1000.0   147.397417  0    1.416667   148.814083   
1         139.235000         1000.0   140.285694  0    1.416667   141.702361   
2         138.031500         1000.0   139.353722  0    1.416667   140.770389   
4         140.721333         1000.0   142.173417  0    1.416667   143.590083   
5         138.706111         1000.0   140.559583  0    1.416667   141.976250   
...              ...            ...          ... ..         ...          ...   
6713      112.963000         1000.0   114.269250  0    1.187500   115.456750   
6714      112.439667         1000.0   114.062583  0    1.187500   115.250083   
6715      111.964333         1000.0   112.389854  1    1.187500   113.577354   
6716      111.102636         1000.0   111.488574  0    1.187500   112.676074   
6717      110.458000         1000.0   111.200187  0    1.187500   112.387687   

        returns  
0    -99.000000  
1      0.952211  
2      0.993423  
4    -99.000000  
5      0.988761  
...         ...  
6713   0.999101  
6714   0.998210  
6715   0.985486  
6716   0.992065  
6717   0.997441  

[6394 rows x 15 columns]

In [62]:
df_filtered = mzf[mzf['returns'] != -99]

In [63]:
df_filtered

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
1     00138GAA7   2021-03-29  20130711.0          2014-01-01   
2     00138GAA7   2021-04-21  20130711.0          2014-01-01   
5     00138GAA7   2021-12-06  20130711.0          2014-01-01   
7     001814AQ5   2021-02-16  19940215.0          1994-08-15   
8     001814AQ5   2021-03-29  19940215.0          1994-08-15   
...         ...          ...         ...                 ...   
6713  989822AA9   2021-08-25  19931020.0          1994-04-15   
6714  989822AA9   2021-09-27  19931020.0          1994-04-15   
6715  989822AA9   2021-10-27  19931020.0          1994-04-15   
6716  989822AA9   2021-11-22  19931020.0          1994-04-15   
6717  989822AA9   2021-12-29  19931020.0          1994-04-15   

      INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  \
1                      6         2030-01-01  20300701.0   8.500   
2                      6         2030-01-01  20300701.0   8.500   
5                      6         2030-01-01  20300701.0   8.500   
7                      6         2023-08-15  20240215.0   7.375   
8                      6         2023-08-15  20240215.0   7.375   
...                  ...                ...         ...     ...   
6713                   6         2023-04-15  20231015.0   7.125   
6714                   6         2023-04-15  20231015.0   7.125   
6715                   6         2023-04-15  20231015.0   7.125   
6716                   6         2023-04-15  20231015.0   7.125   
6717                   6         2023-04-15  20231015.0   7.125   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
1         139.235000         1000.0   140.285694  0    1.416667   141.702361   
2         138.031500         1000.0   139.353722  0    1.416667   140.770389   
5         138.706111         1000.0   140.559583  0    1.416667   141.976250   
7         119.367333         1000.0   119.705354  1    1.229167   120.934521   
8         117.227889         1000.0   117.688827  0    1.229167   118.917993   
...              ...            ...          ... ..         ...          ...   
6713      112.963000         1000.0   114.269250  0    1.187500   115.456750   
6714      112.439667         1000.0   114.062583  0    1.187500   115.250083   
6715      111.964333         1000.0   112.389854  1    1.187500   113.577354   
6716      111.102636         1000.0   111.488574  0    1.187500   112.676074   
6717      110.458000         1000.0   111.200187  0    1.187500   112.387687   

       returns  
1     0.952211  
2     0.993423  
5     0.988761  
7     0.993076  
8     0.983325  
...        ...  
6713  0.999101  
6714  0.998210  
6715  0.985486  
6716  0.992065  
6717  0.997441  

[5568 rows x 15 columns]

# Zeros Part

In [64]:
zeros['C'] = 0

In [65]:
zeros['coupon_amt'] = 0 

In [97]:
zeros['total_value'] = zeros['daily_clean_pr']

In [98]:
zeros['returns'] = -99

In [99]:
# Define dataframe for work on it.
mzf = pd.DataFrame()

for m in zeros["cusip_id"].unique():

    #df for unique cusip_id 
    mf = zeros.loc[zeros["cusip_id"] == m]    
    
    #pd.Series for dates
    dates = mf['trd_exctn_dt'].reset_index(drop=True) 
    
    for i in range(dates.shape[0]-1):
        pastmonth, pastyear = dates[i].month, dates[i].year
        nowmonth, nowyear = dates[i+1].month, dates[i+1].year
        
        # if date pair is suitable to work on 
        if ((pastmonth + 1 == nowmonth) & (pastyear == nowyear)) |  ((pastyear +1 == nowyear) & (pastmonth-11 == nowmonth)):
            past = mf.loc[mf["trd_exctn_dt"] == dates[i]]['total_value'].iloc[0]
            now = mf.loc[mf["trd_exctn_dt"] == dates[i+1]]['total_value'].iloc[0]           
            mf["returns"].loc[mf["trd_exctn_dt"] == dates[i+1]] = now/past
            
    mzf = pd.concat([mzf, mf], axis=0)

In [100]:
df_filtered_zeros = mzf[mzf['returns'] != -99]

In [101]:
df_filtered_zeros

cusip_id trd_exctn_dt  DATED_DATE  FIRST_INTEREST_DATE  \
3884  48130UPE9   2021-02-10  20181019.0                  NaN   
3885  48130UPE9   2021-03-24  20181019.0                  NaN   
3886  48130UPE9   2021-04-28  20181019.0                  NaN   
3887  48130UPE9   2021-05-26  20181019.0                  NaN   
3888  48130UPE9   2021-06-23  20181019.0                  NaN   
3889  48130UPE9   2021-07-28  20181019.0                  NaN   
3890  48130UPE9   2021-08-16  20181019.0                  NaN   
3891  48130UPE9   2021-09-28  20181019.0                  NaN   
3892  48130UPE9   2021-10-27  20181019.0                  NaN   
3893  48130UPE9   2021-11-03  20181019.0                  NaN   
3894  48130UPE9   2021-12-29  20181019.0                  NaN   

      INTEREST_FREQUENCY  LAST_INTEREST_DATE    MATURITY  COUPON  \
3884                 0.0                 NaN  20231016.0     0.0   
3885                 0.0                 NaN  20231016.0     0.0   
3886                 0.0                 NaN  20231016.0     0.0   
3887                 0.0                 NaN  20231016.0     0.0   
3888                 0.0                 NaN  20231016.0     0.0   
3889                 0.0                 NaN  20231016.0     0.0   
3890                 0.0                 NaN  20231016.0     0.0   
3891                 0.0                 NaN  20231016.0     0.0   
3892                 0.0                 NaN  20231016.0     0.0   
3893                 0.0                 NaN  20231016.0     0.0   
3894                 0.0                 NaN  20231016.0     0.0   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
3884      212.480600         1000.0          NaN  0           0   212.480600   
3885      188.570000         1000.0          NaN  0           0   188.570000   
3886      208.840000         1000.0          NaN  0           0   208.840000   
3887      197.500000         1000.0          NaN  0           0   197.500000   
3888      208.680000         1000.0          NaN  0           0   208.680000   
3889      226.090000         1000.0          NaN  0           0   226.090000   
3890      233.590000         1000.0          NaN  0           0   233.590000   
3891      221.990000         1000.0          NaN  0           0   221.990000   
3892      229.933333         1000.0          NaN  0           0   229.933333   
3893      233.388333         1000.0          NaN  0           0   233.388333   
3894      276.030000         1000.0          NaN  0           0   276.030000   

       returns  
3884  0.953384  
3885  0.887469  
3886  1.107493  
3887  0.945700  
3888  1.056608  
3889  1.083429  
3890  1.033173  
3891  0.950340  
3892  1.035782  
3893  1.015026  
3894  1.182707

In [102]:
df_filtered

cusip_id trd_exctn_dt  DATED_DATE FIRST_INTEREST_DATE  \
1     00138GAA7   2021-03-29  20130711.0          2014-01-01   
2     00138GAA7   2021-04-21  20130711.0          2014-01-01   
5     00138GAA7   2021-12-06  20130711.0          2014-01-01   
7     001814AQ5   2021-02-16  19940215.0          1994-08-15   
8     001814AQ5   2021-03-29  19940215.0          1994-08-15   
...         ...          ...         ...                 ...   
6713  989822AA9   2021-08-25  19931020.0          1994-04-15   
6714  989822AA9   2021-09-27  19931020.0          1994-04-15   
6715  989822AA9   2021-10-27  19931020.0          1994-04-15   
6716  989822AA9   2021-11-22  19931020.0          1994-04-15   
6717  989822AA9   2021-12-29  19931020.0          1994-04-15   

      INTEREST_FREQUENCY LAST_INTEREST_DATE    MATURITY  COUPON  \
1                      6         2030-01-01  20300701.0   8.500   
2                      6         2030-01-01  20300701.0   8.500   
5                      6         2030-01-01  20300701.0   8.500   
7                      6         2023-08-15  20240215.0   7.375   
8                      6         2023-08-15  20240215.0   7.375   
...                  ...                ...         ...     ...   
6713                   6         2023-04-15  20231015.0   7.125   
6714                   6         2023-04-15  20231015.0   7.125   
6715                   6         2023-04-15  20231015.0   7.125   
6716                   6         2023-04-15  20231015.0   7.125   
6717                   6         2023-04-15  20231015.0   7.125   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
1         139.235000         1000.0   140.285694  0    1.416667   141.702361   
2         138.031500         1000.0   139.353722  0    1.416667   140.770389   
5         138.706111         1000.0   140.559583  0    1.416667   141.976250   
7         119.367333         1000.0   119.705354  1    1.229167   120.934521   
8         117.227889         1000.0   117.688827  0    1.229167   118.917993   
...              ...            ...          ... ..         ...          ...   
6713      112.963000         1000.0   114.269250  0    1.187500   115.456750   
6714      112.439667         1000.0   114.062583  0    1.187500   115.250083   
6715      111.964333         1000.0   112.389854  1    1.187500   113.577354   
6716      111.102636         1000.0   111.488574  0    1.187500   112.676074   
6717      110.458000         1000.0   111.200187  0    1.187500   112.387687   

       returns  
1     0.952211  
2     0.993423  
5     0.988761  
7     0.993076  
8     0.983325  
...        ...  
6713  0.999101  
6714  0.998210  
6715  0.985486  
6716  0.992065  
6717  0.997441  

[5568 rows x 15 columns]

# Concat 

In [103]:
df_final = pd.concat([df_filtered,df_filtered_zeros],axis=0)

In [104]:
df_final

cusip_id trd_exctn_dt  DATED_DATE  FIRST_INTEREST_DATE  \
1     00138GAA7   2021-03-29  20130711.0  2014-01-01 00:00:00   
2     00138GAA7   2021-04-21  20130711.0  2014-01-01 00:00:00   
5     00138GAA7   2021-12-06  20130711.0  2014-01-01 00:00:00   
7     001814AQ5   2021-02-16  19940215.0  1994-08-15 00:00:00   
8     001814AQ5   2021-03-29  19940215.0  1994-08-15 00:00:00   
...         ...          ...         ...                  ...   
3890  48130UPE9   2021-08-16  20181019.0                  NaN   
3891  48130UPE9   2021-09-28  20181019.0                  NaN   
3892  48130UPE9   2021-10-27  20181019.0                  NaN   
3893  48130UPE9   2021-11-03  20181019.0                  NaN   
3894  48130UPE9   2021-12-29  20181019.0                  NaN   

      INTEREST_FREQUENCY   LAST_INTEREST_DATE    MATURITY  COUPON  \
1                    6.0  2030-01-01 00:00:00  20300701.0   8.500   
2                    6.0  2030-01-01 00:00:00  20300701.0   8.500   
5                    6.0  2030-01-01 00:00:00  20300701.0   8.500   
7                    6.0  2023-08-15 00:00:00  20240215.0   7.375   
8                    6.0  2023-08-15 00:00:00  20240215.0   7.375   
...                  ...                  ...         ...     ...   
3890                 0.0                  NaN  20231016.0   0.000   
3891                 0.0                  NaN  20231016.0   0.000   
3892                 0.0                  NaN  20231016.0   0.000   
3893                 0.0                  NaN  20231016.0   0.000   
3894                 0.0                  NaN  20231016.0   0.000   

      daily_clean_pr  PRINCIPAL_AMT  dirty_price  C  coupon_amt  total_value  \
1         139.235000         1000.0   140.285694  0    1.416667   141.702361   
2         138.031500         1000.0   139.353722  0    1.416667   140.770389   
5         138.706111         1000.0   140.559583  0    1.416667   141.976250   
7         119.367333         1000.0   119.705354  1    1.229167   120.934521   
8         117.227889         1000.0   117.688827  0    1.229167   118.917993   
...              ...            ...          ... ..         ...          ...   
3890      233.590000         1000.0          NaN  0    0.000000   233.590000   
3891      221.990000         1000.0          NaN  0    0.000000   221.990000   
3892      229.933333         1000.0          NaN  0    0.000000   229.933333   
3893      233.388333         1000.0          NaN  0    0.000000   233.388333   
3894      276.030000         1000.0          NaN  0    0.000000   276.030000   

       returns  
1     0.952211  
2     0.993423  
5     0.988761  
7     0.993076  
8     0.983325  
...        ...  
3890  1.033173  
3891  0.950340  
3892  1.035782  
3893  1.015026  
3894  1.182707  

[5579 rows x 15 columns]

In [105]:
df_final.C.value_counts()

0    4642
1     937
Name: C, dtype: int64